<a href="https://colab.research.google.com/github/sclaudiobr/covid2019/blob/master/COVID19_Heatmap.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install --upgrade folium

     |████████████████████████████████| 102kB 3.6MB/s 
ERROR: datascience 0.10.6 has requirement folium==0.2.1, but you'll have folium 0.11.0 which is incompatible.
  Found existing installation: folium 0.8.3
    Uninstalling folium-0.8.3:
      Successfully uninstalled folium-0.8.3


In [2]:
import pandas as pd
import numpy as np
import folium
from folium import plugins
import json
print("Nova versão do Folium: ", folium.__version__)

Nova versão do Folium:  0.11.0


In [3]:
# Aqui, configuramos o acesso ao reposiório e exportação para o formato pandas Dataframe (tabela)
# Observe que aqui usei o terminal LINUX do COLAB para a importacao e descompactação do arquivo.
!wget https://data.brasil.io/dataset/covid19/caso.csv.gz
!gunzip caso.csv.gz
df = pd.read_csv("caso.csv")
df.head(10)

--2020-09-15 17:59:44--  https://data.brasil.io/dataset/covid19/caso.csv.gz
Resolving data.brasil.io (data.brasil.io)... 104.26.8.175, 172.67.71.45, 104.26.9.175, ...
Connecting to data.brasil.io (data.brasil.io)|104.26.8.175|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 7268335 (6.9M) [application/gzip]
Saving to: ‘caso.csv.gz’

caso.csv.gz         100%[===================>]   6.93M  4.15MB/s    in 1.7s    

2020-09-15 17:59:46 (4.15 MB/s) - ‘caso.csv.gz’ saved [7268335/7268335]



date state  ... confirmed_per_100k_inhabitants death_rate
0  2020-09-14    AC  ...                     2968.01919     0.0244
1  2020-09-13    AC  ...                     2966.88531     0.0245
2  2020-09-12    AC  ...                     2964.84435     0.0244
3  2020-09-11    AC  ...                     2948.51661     0.0245
4  2020-09-10    AC  ...                     2934.11646     0.0245
5  2020-09-09    AC  ...                     2910.41857     0.0246
6  2020-09-08    AC  ...                     2890.68922     0.0247
7  2020-09-07    AC  ...                     2887.85455     0.0245
8  2020-09-06    AC  ...                     2884.90648     0.0245
9  2020-09-05    AC  ...                     2880.93794     0.0246

[10 rows x 12 columns]

In [4]:
# Importa dados de localização ponto(lat,long)) das cidades segundo a base de dados do IBGE de 2010
cidades = pd.read_csv('https://raw.githubusercontent.com/sandeco/CanalSandeco/master/covid-19/cidades_brasil.csv')
cidades.head()

codigo_ibge                 nome  latitude  longitude  capital  codigo_uf
0      5200050      Abadia de Goiás -16.75730   -49.4412        0         52
1      3100104  Abadia dos Dourados -18.48310   -47.3916        0         31
2      5200100            Abadiânia -16.19700   -48.7057        0         52
3      3100203               Abaeté -19.15510   -45.4444        0         31
4      1500107           Abaetetuba  -1.72183   -48.8788        0         15

In [5]:
# Aqui fazemos a troca de índice de cidades pelo códifo do IBGE
cidades = cidades.set_index('codigo_ibge')

In [6]:
cidades.head()

nome  latitude  longitude  capital  codigo_uf
codigo_ibge                                                              
5200050          Abadia de Goiás -16.75730   -49.4412        0         52
3100104      Abadia dos Dourados -18.48310   -47.3916        0         31
5200100                Abadiânia -16.19700   -48.7057        0         52
3100203                   Abaeté -19.15510   -45.4444        0         31
1500107               Abaetetuba  -1.72183   -48.8788        0         15

In [7]:
cities = df.loc[df.place_type == 'city',:]
cities.place_type.unique()

array(['city'], dtype=object)

In [8]:
# juntar as duas bases de dados (IBGE cidades) come guardar na variável cities
cities = cities.join(cidades, on='city_ibge_code')

In [9]:
# selecionar as colunas de interesse da tabela "cities", 
# geo_last são os ultimos registros da tabela para cada cidade
geo_last = cities.loc[cities.is_last==True,['city','latitude', 'longitude','state','confirmed','deaths']]
geo_last.head()

city  latitude  longitude state  confirmed  deaths
182    Acrelândia  -9.82581   -66.8972    AC        446       9
346  Assis Brasil -10.92980   -69.5738    AC        560       9
477     Brasiléia -10.99500   -68.7497    AC       1152      19
600        Bujari  -9.81528   -67.9550    AC        371       7
754      Capixaba -10.56600   -67.6860    AC        248       7

In [10]:
#Quantidade de cidades com casos de covid-19
len(geo_last)

5571

In [11]:
#Quantidade de casos confirmados 
geo_last.confirmed.sum()

4302345

In [12]:
#Quantidade de mortes por covid-19
geo_last.deaths.sum()

131082

In [ ]:
#Porcentagem de mortos sobre os casos confirmados
geo_last.deaths.sum()/geo_last.confirmed.sum()*100

3.9564585248175064

In [13]:
# verificar se todos os estados estão inseridos
len(geo_last.state.unique())

27

In [14]:
# Separando o conjunto de dados da interpolação
coordenadas = geo_last[['latitude','longitude','confirmed']]
#retirar as linhas que tiver dados faltando
coordenadas = coordenadas.dropna()
coordenadas.head()

latitude  longitude  confirmed
182  -9.82581   -66.8972        446
346 -10.92980   -69.5738        560
477 -10.99500   -68.7497       1152
600  -9.81528   -67.9550        371
754 -10.56600   -67.6860        248

In [15]:
baseMap = folium.Map(
    width = '100%',   height = '100%',
    location = [-15.77972, -47.92972], # <- Brasil
    zoom_start = 4
)

In [ ]:
baseMap

In [16]:
baseMap = baseMap.add_child(plugins.HeatMap(coordenadas))

In [ ]:
baseMap

In [17]:
# retirar dados faltantes
geo_last = geo_last.dropna()
geo_last.head(5)

city  latitude  longitude state  confirmed  deaths
182    Acrelândia  -9.82581   -66.8972    AC        446       9
346  Assis Brasil -10.92980   -69.5738    AC        560       9
477     Brasiléia -10.99500   -68.7497    AC       1152      19
600        Bujari  -9.81528   -67.9550    AC        371       7
754      Capixaba -10.56600   -67.6860    AC        248       7

In [18]:
for i in range(0,len(geo_last)):
    folium.Circle(
        location = [geo_last.iloc[i]['latitude'], geo_last.iloc[i]['longitude']],
        color = '#00FF69',
        fill = '#00A1B3',
        tooltip = '<li><bold> CIDADE: '+ str(geo_last.iloc[i]['city']) + "</li></bold>" +
                 '<li><bold> ESTADO: '+ str(geo_last.iloc[i]['state']) +"</li></bold>" +
                 '<li><bold> CONFIRMADOS: '+ str(geo_last.iloc[i]['confirmed'])+"</li></bold>" +
                 '<li><bold> MORTES: '+ str(geo_last.iloc[i]['deaths']) + "</li></bold>" ,
        radius = (geo_last.iloc[i]['confirmed']**0.78)
                                            
    ).add_to(baseMap)
#baseMap

In [19]:
# importando logomarca e colocando no mapa
from folium.plugins import FloatImage
url = 'https://raw.githubusercontent.com/sclaudiobr/algoritmos-py/master/text43.png'
FloatImage(url,bottom=10,left=55).add_to(baseMap)
baseMap

In [20]:
baseMap.save('heatmap-cidade.html')